### TODO: add to the requirements.txt

!pip install tweepy==3.10.0 

!pip install requests 

!pip install twython==3.9.1

In [1]:
import json
from twython import Twython, TwythonError, TwythonRateLimitError
import os
import pandas as pd

In [6]:
with open("../bearer_token.txt") as tokens:
    tokens_json = json.loads(tokens.read())
    #os.environ['BEARER_TOKEN'] = token.read()[:-1]
    os.environ['CONSUMER_KEY'] = tokens_json['consumer_key']
    os.environ['CONSUMER_SECRET'] = tokens_json['consumer_secret']
    os.environ['ACESS_TOKEN'] = tokens_json['access_token']
    os.environ['ACESS_TOKEN_SECRET'] = tokens_json['access_token_secret']

In [7]:
consumer_key = os.environ.get("CONSUMER_KEY")
consumer_secret = os.environ.get("CONSUMER_SECRET")
access_token = os.environ.get("ACCESS_TOKEN")
access_token_secret = os.environ.get("ACCESS_TOKEN_SECRET")

In [8]:
twitter = Twython(consumer_key, consumer_secret, access_token, access_token_secret) 

In [9]:
def timeline(user_id, max_id=None):
#       """ 
#   Loop over a user's timeline, starting at max_id. 
#   Generator.
#  
#   We can get up to 15 pages. 
#   This function loops up to 16 times to make the base case 
#   `len(tweets) == 0` trigger.
#   """
    for i in range(16):
        tweets = twitter.get_user_timeline(screen_name=user_id,
                                      max_id=max_id,
                                      count=200,
                                      trim_user=True,
                                      exclude_replies=True,
                                      include_rts=False)
        if len(tweets) > 0:  # last page should have zero results
            for tweet in tweets:
                max_id = tweet['id'] - 1
                yield tweet
        else:
            break

In [10]:
from datetime import datetime
import time

def sleep_until(ts):
 # """ Sleep until the given UTC UNIX TIMESTAMP. """
    next_time = datetime.utcfromtimestamp(int(ts))
    now = datetime.utcnow()
    offset = (next_time - now).seconds
    print("Enhancing calm. Next try: {} (Currently {})".format(next_time, now))
    print("Sleeping for {}...".format(offset))
    time.sleep(offset)
    print("Continuing...")

In [40]:
users_target = [{'user':'BernieSanders',                               
'party':'Democratic Party'         
},
{'user':'ewarren',                 
'party':'Democratic Party'         
},
{'user':'AOC',                     
'party':'Democratic Party'         
},
{'user':'CoryBooker',              
'party':'Democratic Party'         
},
{'user':'KamalaHarris',            
'party':'Democratic Party'         
},
{'user':'SpeakerPelosi',           
'party':'Democratic Party'         
},
{'user':'AlexPadilla4CA',          
'party':'Democratic Party'         
},
{'user':'DickDurbin',              
'party':'Democratic Party'         
},
{'user':'JeanneShaheen',                   
'party':'Democratic Party'                 
},
{'user':'JeffMerkley',                      
'party':'Democratic Party'                 
},
{'user':'JoeBiden',                         
'party':'Democratic Party'                 
},
{'user':'tedcruz',                                
'party':'Republican Party'
},
{'user':'marcorubio',
'party':'Republican Party'
},
{'user':'RandPaul',
'party':'Republican Party'
},
{'user':'MittRomney',
'party':'Republican Party'
},
{'user':'BillHagertyTN',
'party':'Republican Party'
},
{'user':'JohnCornyn',
'party':'Republican Party'
},
{'user':'MarshaBlackburn',
'party':'Republican Party'
},
{'user':'senrobportman',
'party':'Republican Party'
},
{'user':'DanCrenshawTX',  
'party':'Republican Party'
},
{'user':'SteveScalise',   
'party':'Republican Party'
},
{'user':'GOPLeader',      
'party':'Republican Party'
}]                      

In [41]:
fields = ['id', 'user', 'created_at', 'text', 'lang', 'label']
max_id = None
for element in users_target:
    df_test = pd.DataFrame(columns = fields)
    while True:
        try:
            name_user = element['user']
            print(f'############# Scraping {name_user} timeline #############')
            for idx, tweet in enumerate(timeline(name_user, max_id)):
                if (idx+1) % 1000 == 0:
                    print(f'Scanned {idx+1} tweets')
                sub = {k: v for k, v in tweet.items() if k in fields}
                sub['user'] = sub['user']['id']
                sub['label'] = element['party']
                df_test = df_test.append(sub, ignore_index=True)
                max_id = sub['id']
            max_id = None
            break
        except TwythonRateLimitError as e:
            sleep_until(e.retry_after) # sleep until the given date
        except TwythonError as e:
            # I *think* this is caused by protected profiles. 
            # I can read some user profile info, but not the timeline
            print(e)
            print("Skipping...")
            break
    df_test.to_csv(f'../data/{name_user}.csv', sep='|', encoding='utf-8', index=False)

############# Scraping BernieSanders timeline #############
Scanned 1000 tweets
Scanned 2000 tweets
############# Scraping ewarren timeline #############
Scanned 1000 tweets
Scanned 2000 tweets
############# Scraping AOC timeline #############
Scanned 1000 tweets
############# Scraping CoryBooker timeline #############
Scanned 1000 tweets
Scanned 2000 tweets
############# Scraping KamalaHarris timeline #############
Scanned 1000 tweets
Scanned 2000 tweets
############# Scraping SpeakerPelosi timeline #############
Scanned 1000 tweets
Scanned 2000 tweets
############# Scraping AlexPadilla4CA timeline #############
Scanned 1000 tweets
Scanned 2000 tweets
############# Scraping DickDurbin timeline #############
Scanned 1000 tweets
Scanned 2000 tweets
############# Scraping JeanneShaheen timeline #############
Scanned 1000 tweets
Scanned 2000 tweets
############# Scraping JeffMerkley timeline #############
Scanned 1000 tweets
Scanned 2000 tweets
############# Scraping JoeBiden timeline ###

In [57]:
df_test

id      user                      created_at  \
0     1499574005652668418  19739126  Fri Mar 04 02:34:38 +0000 2022   
1     1499496170506313731  19739126  Thu Mar 03 21:25:20 +0000 2022   
2     1499444970280914952  19739126  Thu Mar 03 18:01:53 +0000 2022   
3     1499400353296510994  19739126  Thu Mar 03 15:04:36 +0000 2022   
4     1499193245863227394  19739126  Thu Mar 03 01:21:38 +0000 2022   
...                   ...       ...                             ...   
1121  1374366660463882242  19739126  Tue Mar 23 14:25:21 +0000 2021   
1122  1374166756655128578  19739126  Tue Mar 23 01:11:00 +0000 2021   
1123  1374133229645664266  19739126  Mon Mar 22 22:57:46 +0000 2021   
1124  1374063153923960834  19739126  Mon Mar 22 18:19:19 +0000 2021   
1125  1374039145799114762  19739126  Mon Mar 22 16:43:55 +0000 2021   

                                                   text lang             label  
0     We have:\n- A crisis at our border\n- A crime ...   en  Republican Party  
1     The average price for a gallon of gas is $3.73...   en  Republican Party  
2     Speaker Pelosi: Ban oil from Russia.\n\nAlso S...   en  Republican Party  
3     If Ukraine's Parliament can meet in person in ...   en  Republican Party  
4     719 days since Pelosi closed the People’s Hous...   en  Republican Party  
...                                                 ...  ...               ...  
1121  The losing Democrat candidate in #IA02 admits ...   en  Republican Party  
1122  .@RepMMM won the race in #IA02. Then she won t...   en  Republican Party  
1123  While VP Harris laughs off a humanitarian cris...   en  Republican Party  
1124  Biden's Border Crisis is worsening:\n1️⃣ He wa...   en  Republican Party  
1125  President Biden’s invitations and incentives h...   en  Republican Party  

[1126 rows x 6 columns]

In [42]:
len(df_test[df_test['lang']=='en'])

1120

----------------------------------------------------------------------------------------------------------

# TEST

In [56]:
def timeline_test(user_id, max_id=None):
#       """ 
#   Loop over a user's timeline, starting at max_id. 
#   Generator.
#  
#   We can get up to 15 pages. 
#   This function loops up to 16 times to make the base case 
#   `len(tweets) == 0` trigger.
#   """
    for i in range(16):
        tweets = twitter.get_user_timeline(screen_name=user_id,
                                      max_id=max_id,
                                      count=200,
                                      trim_user=True,
                                      exclude_replies=True,
                                      include_rts=False)
        if len(tweets) > 0:  # last page should have zero results
            for tweet in tweets:
                max_id = tweet['id'] - 1
                yield tweet
        else:
            break

In [55]:
for idx, tweets in enumerate(timeline_test('BernieSanders', max_id=None)):
    print(idx)

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27

1978
1979
1980
1981
1982
1983
1984
1985
1986
1987
1988
1989
1990
1991
1992
1993
1994
1995
1996
1997
1998
1999
2000
2001
2002
2003
2004
2005
2006
2007
2008
2009
2010
2011
2012
2013
2014
2015
2016
2017
2018
2019
2020
2021
2022
2023
2024
2025
2026
2027
2028
2029
2030
2031
2032
2033
2034
2035
2036
2037
2038
2039
2040
2041
2042
2043
2044
2045
2046
2047
2048
2049
2050
2051
2052
2053
2054
2055
2056
2057
2058
2059
2060
2061
2062
2063
2064
2065
2066
2067
2068
2069
2070
2071
2072
2073
2074
2075
2076
2077
2078
2079
2080
2081
2082
2083
2084
2085
2086
2087
2088
2089
2090
2091
2092
2093
2094
2095
2096
2097
2098
2099
2100
2101
2102
2103
2104
2105
2106
2107
2108
2109
2110
2111
2112
2113
2114
2115
2116
2117
2118
2119
2120
2121
2122
2123
2124
2125
2126
2127
2128
2129
2130
2131
2132
2133
2134
2135
2136
2137
2138
2139
2140
2141
2142
2143
2144
2145
2146
2147
2148
2149
2150
2151
2152
2153
2154
2155
2156
2157
2158
2159
2160
2161
2162
2163
2164
2165
2166
2167
2168
2169
2170
2171
2172
2173
2174
2175
2176
2177


In [58]:
import tweepy

In [59]:
auth = tweepy.OAuthHandler(consumer_key, consumer_secret)
auth.set_access_token(access_token, access_token_secret)
api = tweepy.API(auth)

In [60]:
userID = 'BernieSanders'

In [66]:
tweets = api.user_timeline(screen_name=userID, 
                           # 200 is the maximum allowed count
                           count=200,
                           include_rts = False,
                           # Necessary to keep full_text 
                           # otherwise only the first 140 words are extracted
                           tweet_mode = 'extended'
                           )

In [67]:
all_tweets = []
all_tweets.extend(tweets)
oldest_id = tweets[-1].id
while True:
    tweets = api.user_timeline(screen_name=userID, 
                           # 200 is the maximum allowed count
                           count=200,
                           include_rts = False,
                           max_id = oldest_id - 1,
                           # Necessary to keep full_text 
                           # otherwise only the first 140 words are extracted
                           tweet_mode = 'extended'
                           )
    if len(tweets) == 0:
        break
    oldest_id = tweets[-1].id
    all_tweets.extend(tweets)
    print('N of tweets downloaded till now {}'.format(len(all_tweets)))

N of tweets downloaded till now 364
N of tweets downloaded till now 542
N of tweets downloaded till now 739
N of tweets downloaded till now 933
N of tweets downloaded till now 1114
N of tweets downloaded till now 1285
N of tweets downloaded till now 1445
N of tweets downloaded till now 1605
N of tweets downloaded till now 1768
N of tweets downloaded till now 1945
N of tweets downloaded till now 2120
N of tweets downloaded till now 2293
N of tweets downloaded till now 2453
N of tweets downloaded till now 2626
N of tweets downloaded till now 2790
N of tweets downloaded till now 2831


In [92]:
def get_all_tweets(screen_name):
    #Twitter only allows access to a users most recent 3240 tweets with this method

    #authorize twitter, initialize tweepy
    auth = tweepy.OAuthHandler(consumer_key, consumer_secret)
    auth.set_access_token(access_token, access_token_secret)
    api = tweepy.API(auth)
    
    #initialize a list to hold all the tweepy Tweets
    alltweets = []	
    
    #make initial request for most recent tweets (200 is the maximum allowed count)
    new_tweets = api.user_timeline(screen_name = screen_name, count=200, include_rts = False, tweet_mode = 'extended')
    
    #save most recent tweets
    alltweets.extend(new_tweets)
    
    #save the id of the oldest tweet less one
    oldest = alltweets[-1].id - 1
    
    #keep grabbing tweets until there are no tweets left to grab
    while len(new_tweets) > 0:
        print("getting tweets before {}".format(oldest))
        
        #all subsiquent requests use the max_id param to prevent duplicates
        new_tweets = api.user_timeline(screen_name = screen_name,count=200,max_id=oldest, include_rts = False, tweet_mode = 'extended')
        
        #save most recent tweets
        alltweets.extend(new_tweets)
        
        print(new_tweets)
        
        #update the id of the oldest tweet less one
        oldest = alltweets[-1].id - 1
        
        print("...{} tweets downloaded so far".format(len(alltweets)))
    
    #transform the tweepy tweets into a 2D array that will populate the csv	
    outtweets = [[tweet.id_str, tweet.created_at, tweet.text.encode("utf-8")] for tweet in alltweets]
    return(outtweets)
    pass

In [93]:
list_tweets = get_all_tweets('BernieSanders')

getting tweets before 1478853816858599432
[Status(_api=<tweepy.api.API object at 0x7f668e1545b0>, _json={'created_at': 'Wed Jan 05 17:23:46 +0000 2022', 'id': 1478779266804367361, 'id_str': '1478779266804367361', 'full_text': 'The wealthy and powerful corporate interests are trying to create a culture that makes us feel weak and hopeless and diminishes the strength of human solidarity. No. Despair is not an option. Instead, we must rise up together.', 'truncated': False, 'display_text_range': [0, 226], 'entities': {'hashtags': [], 'symbols': [], 'user_mentions': [], 'urls': []}, 'source': '<a href="https://mobile.twitter.com" rel="nofollow">Twitter Web App</a>', 'in_reply_to_status_id': None, 'in_reply_to_status_id_str': None, 'in_reply_to_user_id': None, 'in_reply_to_user_id_str': None, 'in_reply_to_screen_name': None, 'user': {'id': 216776631, 'id_str': '216776631', 'name': 'Bernie Sanders', 'screen_name': 'BernieSanders', 'location': 'Vermont', 'description': 'U.S. Senator for Vermo

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



[Status(_api=<tweepy.api.API object at 0x7f668e1545b0>, _json={'created_at': 'Wed Jan 13 23:28:40 +0000 2021', 'id': 1349498629342580740, 'id_str': '1349498629342580740', 'full_text': 'The House of Representatives has done its job and impeached Donald Trump on a bipartisan basis.\n\nThe Senate must now carry out its constitutional duty and convict Trump to ensure that neither he, nor any other president, can subvert our democracy again.', 'truncated': False, 'display_text_range': [0, 253], 'entities': {'hashtags': [], 'symbols': [], 'user_mentions': [], 'urls': []}, 'source': '<a href="http://twitter.com/download/iphone" rel="nofollow">Twitter for iPhone</a>', 'in_reply_to_status_id': None, 'in_reply_to_status_id_str': None, 'in_reply_to_user_id': None, 'in_reply_to_user_id_str': None, 'in_reply_to_screen_name': None, 'user': {'id': 216776631, 'id_str': '216776631', 'name': 'Bernie Sanders', 'screen_name': 'BernieSanders', 'location': 'Vermont', 'description': 'U.S. Senator for Vermont

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



[Status(_api=<tweepy.api.API object at 0x7f668e1545b0>, _json={'created_at': 'Fri Sep 25 18:02:58 +0000 2020', 'id': 1309554000065441794, 'id_str': '1309554000065441794', 'full_text': 'Do not assume enough people will turn out to vote to defeat Trump and that you can stay home.\n\nEvery vote matters.\n\nMake a plan to vote right now. https://t.co/vMkvkrfLu1', 'truncated': False, 'display_text_range': [0, 170], 'entities': {'hashtags': [], 'symbols': [], 'user_mentions': [], 'urls': [{'url': 'https://t.co/vMkvkrfLu1', 'expanded_url': 'http://vote.org', 'display_url': 'vote.org', 'indices': [147, 170]}]}, 'source': '<a href="https://mobile.twitter.com" rel="nofollow">Twitter Web App</a>', 'in_reply_to_status_id': None, 'in_reply_to_status_id_str': None, 'in_reply_to_user_id': None, 'in_reply_to_user_id_str': None, 'in_reply_to_screen_name': None, 'user': {'id': 216776631, 'id_str': '216776631', 'name': 'Bernie Sanders', 'screen_name': 'BernieSanders', 'location': 'Vermont', 'description'

...

[Status(_api=<tweepy.api.API object at 0x7f668e1545b0>, _json={'created_at': 'Thu May 21 14:44:28 +0000 2020', 'id': 1263480784805081088, 'id_str': '1263480784805081088', 'full_text': 'In my view, life is not about making billions of dollars and not paying attention to the suffering of others. That is a bogus vision. Our job is to recognize our common humanity and ensure that all people live in dignity and security.', 'truncated': False, 'display_text_range': [0, 234], 'entities': {'hashtags': [], 'symbols': [], 'user_mentions': [], 'urls': []}, 'source': '<a href="https://mobile.twitter.com" rel="nofollow">Twitter Web App</a>', 'in_reply_to_status_id': None, 'in_reply_to_status_id_str': None, 'in_reply_to_user_id': None, 'in_reply_to_user_id_str': None, 'in_reply_to_screen_name': None, 'user': {'id': 216776631, 'id_str': '216776631', 'name': 'Bernie Sanders', 'screen_name': 'BernieSanders', 'location': 'Vermont', 'description': 'U.S. Senator for Vermont. Not me, us.', 'url': 'https://

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



[Status(_api=<tweepy.api.API object at 0x7f668e1545b0>, _json={'created_at': 'Tue Mar 03 23:33:21 +0000 2020', 'id': 1234985241879576577, 'id_str': '1234985241879576577', 'full_text': 'Arkansas, Colorado, Minnesota and Texas—your polls are closing in the next few hours. Be sure to get there in time, and if you’re in line when the polls close, stay in line. Check your polling location and hours here: https://t.co/OojGkbvlVe #VoteForBernie', 'truncated': False, 'display_text_range': [0, 256], 'entities': {'hashtags': [{'text': 'VoteForBernie', 'indices': [242, 256]}], 'symbols': [], 'user_mentions': [], 'urls': [{'url': 'https://t.co/OojGkbvlVe', 'expanded_url': 'https://berniesanders.com/vote', 'display_url': 'berniesanders.com/vote', 'indices': [218, 241]}]}, 'source': '<a href="https://mobile.twitter.com" rel="nofollow">Twitter Web App</a>', 'in_reply_to_status_id': 1234977654429769730, 'in_reply_to_status_id_str': '1234977654429769730', 'in_reply_to_user_id': 216776631, 'in_reply_to_

[]
...2831 tweets downloaded so far


AttributeError: 'Status' object has no attribute 'text'